# 2. janomeの使い方(2)
***
[janomeの公式サイト](http://mocobeta.github.io/janome/)を見ながら色々な機能を試してみる。

***
## 2.1 charfilter と tokenfilter

[charfilter](http://mocobeta.github.io/janome/api/janome.html#module-janome.charfilter)
文字ごとに前処理ができる。

[tokenfilter](http://mocobeta.github.io/janome/api/janome.html#janome.tokenfilter.CompoundNounFilter)
Tokenizerした後のtoken毎の処理。
複合名詞を作れたり、残す品詞をリストで指定できる。

charfilter -> tokenizer ->tokenfilter の順で処理するが、
これを纏めて行う事ができるのが　__Analyzer__ である。

In [2]:
#各インポート
from janome.tokenizer import Tokenizer
from janome.analyzer import Analyzer
from janome.charfilter import *
from janome.tokenfilter import *

In [4]:
# Analyzerの設定
char_filters=[]
tokenizer = Tokenizer()
# POSKeepFilterで指定した品詞の語のみ残す事ができる。
token_filters = [POSKeepFilter(['名詞'])]
a = Analyzer(char_filters, tokenizer, token_filters)

In [5]:
tokens = a.analyze('すもももももももものうち')

In [6]:
for token in tokens:
    print(token)

すもも	名詞,一般,*,*,*,*,すもも,スモモ,スモモ
もも	名詞,一般,*,*,*,*,もも,モモ,モモ
もも	名詞,一般,*,*,*,*,もも,モモ,モモ
うち	名詞,非自立,副詞可能,*,*,*,うち,ウチ,ウチ


POSKeepFilterの品詞の指定を変えてみる。

In [7]:
token_filters = [POSKeepFilter(['名詞,一般'])]
a = Analyzer(char_filters, tokenizer, token_filters)
tokens = a.analyze('すもももももももものうち')
for token in tokens:
    print(token)

すもも	名詞,一般,*,*,*,*,すもも,スモモ,スモモ
もも	名詞,一般,*,*,*,*,もも,モモ,モモ
もも	名詞,一般,*,*,*,*,もも,モモ,モモ


このように、前方から一致させている。

POSStopFilterに変更すると、上で拾えなかったものを拾える。

In [8]:
token_filters = [POSStopFilter(['名詞,一般'])]
a = Analyzer(char_filters, tokenizer, token_filters)
tokens = a.analyze('すもももももももものうち')
for token in tokens:
    print(token)

も	助詞,係助詞,*,*,*,*,も,モ,モ
も	助詞,係助詞,*,*,*,*,も,モ,モ
の	助詞,連体化,*,*,*,*,の,ノ,ノ
うち	名詞,非自立,副詞可能,*,*,*,うち,ウチ,ウチ


token_filtersに入れたものは、前から順番に実行される。

TokenCountFilter()は出力が独自のものに変わってしまうため、最後にしか使用できない。

> This filter must placed the last of token filter chain because return values are not tokens but string-integer tuples.

In [9]:
token_filters = [POSKeepFilter(['名詞,一般']),TokenCountFilter()]
a = Analyzer(char_filters, tokenizer, token_filters)
tokens = a.analyze('すもももももももものうち')
for token in tokens:
    print(token)

('すもも', 1)
('もも', 2)


ExtractAttributeFilter()も同様に最後にしか使用できない。

In [10]:
token_filters = [POSKeepFilter(['名詞,一般']),ExtractAttributeFilter('surface')]
a = Analyzer(char_filters, tokenizer, token_filters)
tokens = a.analyze('すもももももももものうち')
for token in tokens:
    print(token)

すもも
もも
もも


***
## 2.2 URL、Twitterユーザー名の削除

charfilter の RegexReplaceCharFilter() を使用し、正規表現でURL、Twitterユーザー名の削除を行う。

URL検出の正規表現：　http(s)?://([-\w]+\.)+[-\w]+(/[-\w ./?%&=]*)?

    ():グループ化
    
    []:繰り返しの対象またはいずれかの要素。[-\w]は、-か英数字
    
    \w:[a-zA-Z0-9_]
    
    ?:0または１回
    
    +:1回以上の繰り返し
    
    *:0回以上の繰り返し
    
Twitterユーザー名検出の正規表現：　@([\w]+)

In [12]:
char_filters=[UnicodeNormalizeCharFilter(),RegexReplaceCharFilter('http(s)?://([-\w]+\.)+[-\w]+(/[-\w ./?%&=]*)?','')]
a = Analyzer(char_filters, tokenizer, token_filters)

In [13]:
import codecs
with codecs.open('tweet.txt','r','utf8') as f:
    text=f.read()
    tokens = a.analyze(text)
    for token in tokens:
        print(token)

futao
suzuki
e
女の子
pef
ichiroozawa
昨晩
無料
スカ
ライブ
net
動画
YouTube
回数
岩
予算
無料
番組
フォロワー
フォロワー
事
気
フォロワー
フォロワー
繋
たい
歌い手
OX
yamapon
bot
o
はなし
ばん
はなし
GTA
Reia
ゲーム
RT
人
期間
月
月
DM
chigaya
ymn
cp
目
RanNan
sino
beaty
美容
雑誌
ファッション
既製
サンプル
得
美的
ROSY
美人
花
リンネル
koamesaku
学校
テーマ
ユニット
bw
zeitaku
贅沢
おすそ分け
キャンペーン
残り
bw
リツイート
贅沢
贅沢
Care
mihonibu
kosakana
寸劇
里
萌
P
extember
ブラック
ジャック
PTA
RYUZi
WORLD
トーク
ゲスト
歌
RYUCHELL
月
楽しみ
HmwwQrUitYhf
お家
子
親
人
親
ricogbs
媚薬
おかげ
感度
体
イッ
fujimoto
akiko
lawson
カスタード
無料
リツイート
カスタード
ウチカフェ
five
胸
ちょうちょ
ドラミング
ゴリラ
SEJ
プレミアム
ナッツ
食
キャラメルアイスバー
税込
キャラメル
アイス
食
ナッツ
食
ダブル
商品
https
dhLFlkKA
E
mJ
久々
ツイート
Bonds
ostrichegg
v
黒
歴史
水
yua
i
yua
is
ジャ
ニーズ
WEST
黄昏
流星
ward
atamotonu
タヌキキツネクマ
mnkiyuske
トラウマ
女子
中学生
女の子
同級生
目
電車
飛び込み
画像
ぱりさまるだよね
nutsinshell
デヴィ
夫人
席
神
レベル
コミュニケーション
スキル
sasamachi
namaste
漫画
アラサー
初恋
midorin
tezostokyo
テゾス
UEX
CMC
通貨
ドミノ
okasanman
大使館
件名
パジャマ
猫
パーティー
猫
パジャマ
クッキー
画像
パーティー
事態
t
co
VFvOp
negoto
kanzeme
とこ
他
ゲーム
差
ahan
McDonaldsJapan
永遠
定番
マックフライポテト
新鋭
カケテミーヨ
カルボナーラ
派
人
クーポン

コミック
VR
ririna
t
妹
JC
SNS
モデル
鍵
垢
人
鍵
メッセージ
torutetto
kiyotaki
bokebot
車
親
hai
furi
app
色紙
キャンペーン
アカウント
ツイート
RT
色紙
艦隊
バトル
ピンチ
VXGHv
hellogoodbye
臣
シーン
怪物
RT
sizumi
nemuri
絵描き
ネタ
ガチ
ネタ
TwiGentle
ペニーワイズ
草
wwwww
ココ
神
モテ
人
メッセ
wwww
パコパコ
性欲
t
co
nyWJ
VenomMovieJP
ヴェノム
プレミア
ブラック
カーペット
イベント
アカウント
ゲスト
armadeus
matoi
inuki
ハァハァ
さび
歌
生放送
バーチャル
YouTuber
カガスタ
貫
GalaxyMobileJP
GalaxyNote
キャンペーン
最新
機種
Galaxy
Note
豪華
賞品
チャンス
CM
miyaevo
ToshikiMasuda
ハァイッ
ラッキィィィィィィィィィィィィィィ
REiO
yuda
alta
早め
お茶
休み
Д
Kiyo
haya
jp
ニローニタイム
横
ハンパ
相手
誰か
ニローニタイム
はん
はん
hQTvPIdYc
Starryheavens
p
テント
nagatsumajuri
コラボ
スープ
カレー
geromamire
D
ID
Lv
リヴァイアサン・マグナ
Tang
MinhyukJapan
ミニョク
地下鉄
カップ
ホルダー
ラッピングバス
スローガンイベントミニョク
MONSTA
モネク
トラウマ
女子
中学生
女の子
同級生
目
電車
飛び込み
画像
t
co
cEFtZ
Swiftie
rin
ツイート
曲
お金
taylor
楽曲
無料
ファン
jyaga
月
si
MAHOTONNN
動画
番号
ヤクザ
マジギレ
t
co
kyon
LArcemovienmeig
人生
ピーマン
肉
ピーマン
aru
野性
爆弾
ー
ー
けい
柄
レオタード
Twitter
Umabi
Official
ー
けい
シェア
ダイヤ
日記
月
ダイヤ
ダイヤ
シェルミー
ダイヤ
サイコロ
ブラックホール
ブラックホール
マス
ZoA
DjJzjAR
gamers
no
gema
フィギュア
下半身
フィギュ

絵
お茶
psqsre
ヨルシカ
歌
クオリティ
ヨルシカ
歌い手
MIX
絵師
動画
RT
RT
人
全員
フ
konoka
ssshinako
koaku
hks
trnk
アプリ
出身
先輩
AKANE
トラウマ
女子
中学生
女の子
同級生
目
電車
飛び込み
画像
t
co
huGX
Parksunhaa
ozora
akiko
lawson
カスタード
無料
リツイート
カスタード
ウチカフェ
yuu
nanase
モバマス
ブレスオブファイア
yokotomo
McDonaldsJapan
シナモンメルツ
スイーツ
身
心
ホット
t
co
iku
nayaka
繰り返し
お金
余裕
お金
興味
Cherry
monety
ゴシック
kokuden
出来事
道理
キット
mirin
soraneko
嘘
冬
地球
生命
P
soulflowerunion
街
ヘイト
男
ipuusan
プリンツ
おみ足
aimheartjpn
会場
魔女
原画
個展
原画
IWJ
sokuhou
身
木
国内
世論
トランプ
大統領
習近平
国家
主席
覇権
身
国際
情報
局長
jpLove
m
人
スパム
人物
想
画面
シリーズ
moririn
skream
japan
RT
オルタナ
ギター
バンド
ポスター
色紙
st
ミニ
アルバム
動画
メッセージ
kmxxxas
すき
miimii
POINT
賞品
LINE
プリペイドカード
アイス
可
方法
RT
締切
フォロワー
サイト
欄
BfVHs
多分
鏡
民
very
RcX
suzuk
hyte
onlyKSK
ShitaoMiu
PRODUCE
KnGlg
kawaii
gensen
d
意地
股
ネコ
masa
コラボキャンペーン
缶
カリー
reika
yuta
nogizaka
ニュース
ジャケット
nd
シングル
帰り道
遠回り
ジャケット
写真
t
co
pULZNVaY
yunhanwang
おばさん
おじさん
おじさん
奥さん
赤ちゃん
時代
日本人
お茶
日月
茶
機械
素材
歴史
kabuturnip
ジジ
stere
SZYVOsJuuWPJexa
TPP
アベ
ケツ
孔
TPP
国家
主権
法律
外資
TPP
ISD
条項
国際
裁判所
憲法
詰まり
立法
司法
外資
手
enu

ginga
povi
c
o
ヨウヤク
会
エマシタネ
なべ
ボイ
部屋
sO
yiOKbx
G
megohime
数字
フミフミ
スヤァ
HjY
iSLdaygB
you
dai
エイト
タッキー
口
横
カメラ
目線
精神
Hey
イケメン
Jr
い
写真
カッコ
お気に入り
リン
ハロウィン
モード
ー
ワンドリ
poledancer
qUT
dr
gGL
女子
Kimidori
McDonaldsJapan
好評
シナモンメルツ
カフェ
タイム
ホット
コーヒー
S
サイズ
無料
t
co
XY
kirari
Tomy
ORpoPceDkhMrfsW
動画
顔出し
人
DM
裏
垢
女子
裏
垢
男子
裏
垢
オフパコ
ON
ULs
McDonaldsJapan
RT
モンストオリジナルマックカード
ゲット
チャンス
オラゴニックリツイート
kujirarara
ぷぇ
wakanaJ
ツーチー・イー
GPS
スケアメ
男子
昨季
冬季
五輪
栄誉
SP
家
模様
FS
ノリ
感じ
ykhre
性
被害
女性
スクショ
何様
裁判
asagiiro
emeth
ノリ
t
co
oJ
u
you
D
C
B
ID
Lv
ティアマト・マグナ
エア
LCrhhC
Gepa
KiehlsJP
肌
キールズ
ロングセラー
美容
オイル
肌
ダメージ
間
美容
オイル
肌
キールズ
Twitter
amp
RT
canabiss
会場
SHOW
CASE
料金
ドリンク
予
Matchapurin
animayell
anime
アニメ
サイト
期間
無料
サイト
アニマエール
DefenceSoul
ディフェンス
事前
キャンペーン
豪華
賞品
方法
アカウント
DefenceSoul
ツイート
RT
rilakkuma
gyr
リラックマストア
スーベニア
アイテム
しっぽ
カワイイ
キタキツネ
リラックマ
ぬいぐるみ
t
co
takarakuji
qoo
豪華
賞品
キャンペーン
takarakuji
qoo
対象
ハ
Meiship
UK
娘
見納め
舞台
娘
銀
ss
フォロワー
アークス
rt
minnano
dougaww
tamago
nupi
seikei
絵
作者
恥
風潮
自分
容姿
悪口
人
暴力
人
罪
ホ
RPG
イベント
t
co
IObs

針金
小学生
menou
azaz
ovo
偏見
並び
hHFhcEsVd
YYb
IkemenVampire
テオドルス
本編
QUO
カード
RT
キャンペーン
対象
本編
吸血
シーン
スチル
QUO
カード
IkemenVampire
ツイート
Taco
ka
漫画
Arutau
ゆかり
パーカー
葵
ゆ
ゆ
ゆ
茜
葵
ゆかり
葵
招
Foooo
tdm
タグ
初心者
気
QurYSH
zS
Medea
ー
ー
MAHOTONNN
動画
番号
ヤクザ
マジギレ
t
co
弓
パーツ
色
塗料
OmqJ
大型
ビジョン
ジェジュン
LAVENDER
Sign
YourLove
動画
スクショ
wako
コマ
部屋
キャベツ
神
ねこ
先生
ポーチ
t
Aow
gYS
R
JRKEV
l
eozEJ
E
ID
Lv
グリームニル
実況
最初
草むら
レベル
ポケモンルビー
実況
part
t
co
da
inatake
yu
h
ータイム
ー
Twitter
写真
ひな
たん
NGT
フォト
写真
ー
マスカット
グループ
メンバー
koku
kuroi
あんさん
スターズ
沢
倭
忍
TDC
倭
ツーショット
H
R
FarbenOrigami
ミリタリー
ちゃん
万国
ooohiy
Riooo
ひよこ
みかん
ひより
萌
ぇ
萌
ぇ
本当
takebee
okurrmr
条
アカネ
最高
泥
最高
最高
o
dATRgD
c
Er
カラース
ーカラース
カラフル
カラス
ASAHI
YUNA
A
応
P
秋
アニメ
情報
盛りだくさん
SHOWROOM
ハロウィン
衣装
届け
ネット
nightgliders
シャインマスカット
うま
sikiomo
ウチカフェスイーツ
クーポン
クーポン
コード
C
使い方
チケット
相互
長期
ア
バン
テ
ィー
ズ
U
F
ES
単発
ア
バン
テ
ィー
ズ
下記
画像
ジャンル
クレカ
身分
貸出
pes
suke
yumana
takagi
ご飯
場所
SKE
映画
アイドル
SASAMI
WaskaRobin
pro
期間
方法
ツイート
sasa
tech
ぁ
幕張
感じ
チームベビメタ
缶
バッジ
デス
ラバー
バンド
幕張
イジメダメゼッタイ
LightStuart
kikumaco
税率
政権
党
最高

...

部門
ラノベ
素
著者
CULdela
Shinjiro
Ikari
割
声
名義
ジャンヌ
オルタ
kinchan
TokiBosi
月
夜明け
瑠璃
お姫様
アニメ
ネット
キャベツ
画像
お祭り騒ぎ
w
arashi
女子
ROOKiEZ
Today
pm
baby
赤目
金髪
ハロウィン
w
絵描き
unaju
ut
an
RO
GEAEr
sakasanoshippo
jusjusojus
hobby
magazine
紅
豚
ポルコ
カーチス
マンマユート
ボス
魅力
男
コレクション
フィギュア
シークレット
種類
ジブリ
爽怪人
ワン
シーン
bocnico
気分
リュック
派
目覚まし
EX
曲
ナンバー
譜面
曲
曲
リザルト
癖
赤
higemore
次
ソーダ
ェ
ツマミ
ェ
animatecafeinfo
ドコ
有償
特典
番組
キーホルダー
手
アニメイトカフェグラッテコラボ
月
サイコー
ドリカ
キャンペーン
d
太陽
トマト
麺
with
チーズ
きのこ
ポタージュ
トマト
麺
mashguitar
DoGeZa
to
you
迫力
ヤバ
RT
ハズレ
夢
くじ
妖精
チャンス
夢
t
co
rpCi
NjTb
ugDjDYOM
A
トラウマ
女子
中学生
女の子
同級生
目
電車
飛び込み
画像
ergaisuzu
煉
チュン
レンガ
煉
チュン
キャラ
レンガ
キャラ
レンガ
建物
背景
EBRI
セラミック
アート
センター
煉
ネコミミ
小麦
レンガ
宝物
nakayasumi
horimari
ライブ
招き
リリイベ
レ
ボルト
思い
tsk
ntmnuta
飛行機
手下
マルフィ
ジャック
ハート
tikc
adaruto
douga
女子大
姿
NTR
レ
プ
Iamnoma
ぅ
x
MPufk
dotoll
e
k
ウチカフェスイーツ
クーポン
クーポン
コード
C
使い方
t
co
SJ
vwM
P
kmiyoshi
mei
ひとり
オーディション
締め切り
yutokanan
shamotr
紅茶
季節
砂糖
代わり
キャンディス
香り
シロップ
氷砂糖
宝石
甘み
香り
ティー
バッグ
紅茶
店
味
カルディ
ホ
RPG
キャラ
T
M
shiro
友達
美男
美女
垢
人
RT
雰囲気
人
RT
RT
人
全員

時点
tune
全員
mosika
suji
肉
棒
蜜
壷
至福
ひと時
庭園
街
身体
びふたりきりの
空間
ふたり
愛人
背徳
快楽
愛人
快楽
km
oe
ug
hu
思い出
漫画
McDonaldsJapan
レギュラー
チキンフィレオ
バリュー
ランチ
ー
サシ
手
ランダム
RT
ー
特製
カード
colus
memenekoten
初日
あと
物販
猫
花
meteor
signet
無断
愛
メディア
欄
自体
ツイート
IDEALCUT
プラス
ライブトレカ
yusa
立ち回り
ゴミキルレ
学者
ー
あと
箒
ドア
jimin
BTS
sioopaoo
ホテル
泊まり
kyohei
KadenaAirBase
J
中将
月
基地
F
事故
パイロット
航空
基地
救難
隊員
勲章
HANA
Takato
HW
TzXMM
maigomap
迷子
猫
MapNo
ひまわり
興
寺
H
迷子
メス
猫
額
スペード
サクラ
耳
首輪
名札
Annulaire
久々
姉妹
satomimi
ライン
画像
ボイメ
手始め
yayuyo
ya
夜桜
所行
ご飯
サプライズ
ぅ
Y
utona
SocialGameInfo
インターネット
快感
フレーズ
CLIMAX
キャラ
t
co
dekoiliwo
スプラトゥーン
動画
ーーー
L
リール
ガン
D
ブキ
スプラトゥーン
新人
Vtuber
Vtuber
バーチャル
Youtu
思いつき
nonononn
SEJ
うち
ハロウィン
RT
キャンペーン
RT
キャンペーン
ハロウィン
商品
ハロウィンスイーツ
RT
sora
w
バビ
バビ
身長
OidnS
mottyie
ソシャゲ
感覚
人間
天使
漫画
Akira
Shino
絵
Doomtiruno
etoile
禁書
レベル
馴染み
言葉
NT
美男
美女
雰囲気
人
RT
RT
人
全員
HRH
絵描き
絵描き
絵
大会
最後
自画像
F
BTS
twt
QZQZ
思い出
BTS
hope
jk
何事
ジミン
何事
飯
乳
おっぱい
エロ
旦那
家事
爆乳人
妻
キッチン
SEX
t
co
p
o
FN
得
実績
得
複数
割
コイン
最大
レベル
プレイヤー
レベル
ルビー
スキル
マックス
podoron
ジョジョ
カッコ
ダンサー
音楽

イヤ
フォン
片耳
椿
スマホ
Bluetooth
イヤ
フォン
www
ガチ
ichigohiwata
akiko
lawson
カスタード
無料
リツイート
カスタード
ウチカフェ
life
月
旧暦
月
神嘗祭
かんな
さい
年
新米
神様
祭典
暦
aeaupkr
www
serahan
貴様
模型
魂
study
i
サングラス
雰囲気
setsunas
ziru
asuki
写真
ビッチ
絢
斗
Photo
emeraldcoast
pe
n
名前
chi
xx
torihiki
あん
スタ
ブロマイド
ブロ
緒
紅
郎
泉
アド
ニス
泉
声
biwako
shiga
夜ふかし
夜ふかし
メジャー
語尾
たい
湖
ZeroE
A
津波
原発
地下
リカバリー
段階
ヘリ
政権
震災
UsdIXm
gHjTK
トラウマ
女子
中学生
女の子
同級生
目
電車
飛び込み
画像
t
co
yakanturuturu
konome
ao
肩
写真
ー
uminum
ゃんおにぃたまありがとう
CV
ょぅじょあの
UTX
chikushi
自己
娘
専門
カメラマン
父
娘
写真
自分
手
カメラ
人生
始まり
親
yoniichi
返信
マン
mikuawa
dragonknight
感想
パフォーマンス
曲
歌
歌声
笑顔
shirokanesai
白金
お笑い
芸人
動画
芸人
コーナー
芸人
アカウント
リプ
期限
リプ
O
O
年
年
J
冬
コ
東
ド
ー
ス
テ
め
場
め
ゃ
hypnosismic
LocoLoco
ファイル
シール
A
D
ID
Lv
ゴッドガード・ブローディア
tsubakiya
tea
猫
ゅ
パッケージ
猫
口
koiddon
最多
短編
アニメーション
映画
ロープ
想い
secar
LS
nagoya
MV
t
co
定番
キャンペーン
はずれ
月
Arashi
FanCom
姿勢
ゴリラ
vine
嵐
ジャニ
k
t
co
lNactv
U
catyann
KS
チョコレート
ミルク
牛
牛乳
義務
dY
H
InsecTarpon
ねこ
幼虫
volpixyz
チーズ
チッタ
噴水
広場
チーズ
店
種類
他
種類
ランチタイム
プレート
Imouto
Anime
マモ
ゾンビランドサガ
マモ
kumacchi
ツ

坂
車
マジワロチ
わら
動画
M
gorakubu
tub
pad
aaayk
BunAl
PR
鋼
錬金術
コラボ
TwitterRT
キャンペーン
ゲーム
アイテム
特務
司書
全員
対象
ツイート
ツイート
期限
月
japaaan
com
ドーーーン
ワケ
ぐろのおはぎ
スシロー
寿司
スシロー
グルメ
Reuters
co
jp
路上
法律
字幕
t
co
GNC
N
WH
sirokuro
ked
おしり
指輪
うた
in
yakko
slime
ろう
ぃん
リムソウ
まんが
PKsLP
AlFF
Y
JILLPRINCE
jp
動画
M
ガチ
M
ロスト
M
最低
Romeo
動画
アカウ
XbJNGEpchmUda
lawsonstore
ぶつ
リツイートキャンペーン
lawsonstore
リツイート
オリジナルトート
シリーズ
ローソンストア
キャフリ
myuuun
ウチカフェスイーツ
クーポン
クーポン
コード
C
使い方
okaerisonodakun
リツイート
サンプル
秋祭り
ミニハンドタオルセット
まわり
お子様
サイズ
リツイー
nhk
news
アライグマ
nhk
nhk
御三家
ゲト
tikuwaneko
日課
小学校
同級生
店
小学校
同級生
西口
神輿
モツ
josoul
yukiysd
夏
アシスタント
MC
アリーナ
Be
ジャンヌ
狙い
個人
大当たり
アタランテ
光り物
奇跡
女子
canana
mk
乳
縄
レポ
漫
fumifumi
絵の具
顔料
水彩
aimheartjpn
持ち帰り
お方
がれ
万が一
原画
ma
ツイート
ひさし
ぁぁぁ
髪
hiskm
s
shamotr
紅茶
季節
砂糖
代わり
キャンディス
香り
シロップ
氷砂糖
宝石
甘み
香り
ティー
バッグ
紅茶
店
味
カルディ
kiryu
official
龍
単独
グッズ
Tシャツ
月
扇子
Tシャツ
詳
jun
ryually
個人
情報
被害
LINE
chixida
ふたり
鳩
手下
ジャック
ハート
スキャター
masagodzilla
sdfukuokagirls
扉
Rock
曲
余念
紫
アイドル
所長
ー
ハカタダンスホールベイベー
tarao
女子
Lulua
FortniteBR
Momo
TWICE
FN
自分
パ

グッズ
NEC
jp
amp
LotasMm
秋
季節
暗闇
季節
ダブルパンチトリプルパンチ
自分
自分
心
外
景色
おかげ
cds
小学校
アルマーニ
制服
公立
公共
概念
土地
建物
不動産
文教
地区
パチンコ
次元
南
先
心
大人
AI
機械
AI
最後
人間
手順
逆
基準
機械
nobuta
araraarara
秋
続編
in
ジェジュン
ドラマ
フォトピ
toarunisinoyuk
usedoor
機種
カードケータイ
ワンナンバーフォン
カードケータイ
KY
L
ガラケープラン
実質
ワンナンバーフォン
eSIM
月額
回線
子
Perfume
ぴょんゆか
Perfume
Perfume
人
フォロバ
Tilfinning
ブラック
クローバ
hanamomoV
月
s
weet
丹頂
巫女
ちび
雪
姉妹
ココ
目
MDD
jinnao
フォロワー
k
m
Eisya
余命
月
山奥
マーレ
人
お迎え
リツイート
お迎え
マン
塾
ー
ツイート
足
チャック
SNS
話題
motto
motogp
写真
ホント
ピアニスト
ザルコ
イベント
pon
RT
禁
DBBDA
ID
Lv
takumi
nanoyet
手
ブレ
心
女神
想い
格好
とも
https
arico
ぉ
時差
ぉ
syo
kushino
yui
バナー
特典
コミコミスタジオ
rinrinpika
no
oogiri
ジューシー
CGdrawing
tsubakiya
tea
猫
ゅ
パッケージ
猫
口
takarin
NHK
替え歌
いなかっぺ
大将
ふたつ
不埒
嘘
物
未来
天
天
天下
売国
NHK
弱腰
オベンチャラ
北
南
c
fOjXAc
OTvCJ
yakyuuhamu
素振り
FGO
幕間
物語
キャンペーン
ニキ・パライソ・エルバサ・
段
胤
宝
敵
T
スキル
アサ
性能
amp
クリ
威力
T
kenshoukenshou
動画
ShumitectJapan
シュミテクト
歯ぐき
気
シュミテクト
歯
ケア
ススメ
過敏
症状
歯
ダブル
シュミテクト
史上
最大
濃度
フッ素
歯
ツイート
buildgmk
tosihi
IV
ガルパン
おじさん
年内
一つ
aks
ry
ウチカフェスイーツ
クーポン
クーポン
コード
C
使い方
yu

In [14]:
char_filters=[UnicodeNormalizeCharFilter(),RegexReplaceCharFilter('http(s)?://([-\w]+\.)+[-\w]+(/[-\w ./?%&=]*)?','')]
token_filters = [CompoundNounFilter(), LowerCaseFilter(), POSKeepFilter(['名詞']),TokenCountFilter(att='base_form')]
a = Analyzer(char_filters, tokenizer, token_filters)
with codecs.open('tweet.txt','r','utf8') as f:
    text=f.read()
    tokens = a.analyze(text)
    for token in tokens:
        print(token)

('futao02', 1)
('rt', 7386)
('@suzuki_0314e:', 1)
('女の子', 112)
('peg_pef_peg', 1)
('@ichiroozawa:', 1)
('昨晩', 1)
('ウルグアイ戦直後', 1)
('無料配信', 5)
('スカサカ!ライブ.net', 1)
('レビュー動画', 1)
('youtube上', 1)
('視聴回数2万回', 1)
('岩政さん', 1)
('清水さん', 1)
('試合分析', 1)
('こと', 414)
('cs放送局', 1)
('予算', 1)
('無料配信番組', 1)
('製作', 3)
('...', 1063)
('darekasanno_', 1)
('次第', 3)
('たくさん', 34)
('反応お願い', 1)
('(', 219)
('..)"', 1)
('#フォロワーさん', 4)
('フォロワーさん', 23)
('私', 191)
('事気', 1)
('方', 345)
('繋', 5)
('たい', 2)
('#歌い手好き', 1)
('ox42477139', 1)
('@yamapon_bot:', 12)
('(^o^)', 12)
('さ', 104)
('山本アットホーム', 12)
('はなし', 25)
('今回', 63)
('ばん', 12)
('slot_kantakun', 1)
('@gta5_reia:', 3)
('仕事', 50)
('ゲーム', 16)
('時間', 66)
('人', 342)
('中', 98)
('もの適当', 3)
('当選率2倍', 3)
('フォロー', 99)
('3倍', 4)
('抽選', 135)
('ff内優先', 3)
('誰', 57)
('参加', 154)
('期間', 6)
('10月31日', 9)
('当選者', 11)
('11月1日', 3)
('3日', 4)
('dm', 47)
('chigaya808', 1)
('@ymn_cp:', 1)
('目', 124)
('rippa_puritty', 1)
('@rannan_8903:', 2)
('gorituru_madygn', 1)
('@sino_beaty:', 1)
('来

('マス', 2)
('廃止', 4)
('...。...', 2)
('zoa56djjzjar281', 1)
('@gamers_no_gema:', 1)
('フィギュア', 3)
('下半身フィギュア付きモバイルスタンド『#ケイタイ娘', 1)
('akihabaraゲーマーズ本店&オンラインショップ', 1)
('好評発売中!ゲーマーズ特典', 1)
('白or黒ストッキング', 1)
('付け', 7)
('♪白ストッキング付⇒', 1)
('@yomi_slime', 1)
('抽選結果', 56)
('お伝え', 95)
('ウチカフェスイーツ20円引クーポン', 52)
('!クーポンコード', 52)
('c01612161', 52)
('利用', 64)
('10/30', 52)
('♪使い方⇒://t.co/ejslbtekrq', 1)
('amo_j38', 1)
('@ske48movie_tbs:', 2)
('!映画オフィシャルグッズ', 2)
('お知らせ', 77)
('リストバンド', 2)
('印字', 2)
('アルファベット', 4)
('意味', 26)
('#映画アイドル#ske48', 2)
('https://...', 36)
('i_could_be_free', 1)
('@r1_2674:', 1)
('cafe', 1)
('heartful', 1)
(':', 22)
('半分', 5)
('総集編', 1)
('![', 2)
('#原田知世', 1)
('#半分', 1)
('://t.co/yco5caqwuj', 1)
('tokyo_clubguide', 1)
('club', 4)
('diana', 1)
('show', 5)
('coupon', 1)
('image,', 1)
('f¥1,000/2d!#diana', 1)
('#nightclub', 1)
('#ginza', 1)
('0814___saya', 1)
('@i999iio5', 1)
('parakeet_rabbit', 1)
('@yaribu_anime:', 2)
('キャラソン', 2)
('ぇりー味', 2)
('本日発売', 11)
('三者三様', 2)
('歌声', 9)
('

('通り平和', 1)
('k28wv8i8dcthei8', 1)
('@ldh10443786:', 1)
('ゆず', 1)
('三代目', 1)
('#臣隆', 1)
('h52800050', 1)
('@nenesamagatizei:', 12)
('#今', 12)
('ムシキング', 12)
('後世', 11)
('名曲', 14)
('minto_rumi', 1)
('@yuetunaatm:', 1)
('アルケミスト', 1)
('干支', 1)
('(10/17現在実装文豪', 1)
('misakiinu426', 1)
('lunaticace', 1)
('@kotodaman_pr:', 2)
('緊急告知!!】10/29', 1)
('予定', 19)
('言霊祭', 2)
('5コトダマン', 1)
('抽選確率', 1)
('全体', 1)
('10%', 2)
('...『“超', 1)
('kimorisan', 1)
('直前', 9)
('ysl発表', 1)
('トンデモテンション', 1)
('smoke', 1)
('かわり', 1)
('ゴトーさん', 1)
('定休日', 1)
('前回', 7)
('揺らぎみたい', 1)
('演出', 13)
('eエリア', 1)
('演奏...', 1)
('kimutoko', 1)
('@frontale_staff:', 3)
('今回一番ノリノリ', 2)
('選手', 28)
('不死身', 2)
('怪物', 2)
('ソンリョン', 2)
('特殊メイク', 2)
('本気度', 2)
('違和感ゼロ', 2)
('子どもたち', 3)
('!!」', 6)
('メイク', 5)
('まま帰宅', 2)
('プロモ', 2)
('#frontale...', 2)
('soranogarden', 1)
('@motocchi26:', 1)
('素直', 7)
('程', 5)
('簡単', 19)
('ほんと', 4)
('ひとつ', 14)
('大切', 27)
('bananabox112', 1)
('オーストラリア', 3)
('ロング', 2)
('リーフ', 1)
('ビーチ', 1)
('シドニー', 1)
('北部', 2)
('

('#dancerush_stardom#ダンスラッシュ振り付け参考:', 1)
('猫さん', 1)
('loup_fraise', 1)
('@njcaeqy4gciws7p:', 1)
('ぅー!', 1)
('神絵師✨', 1)
('ぉぉぉ', 1)
('yatoukyoutou555', 2)
('@zcy6kgkag6xgmvx:', 1)
('@onagamasatoshi', 1)
('遊具', 1)
('100ヶ所以上放置', 1)
('陣営', 2)
('田中慧氏', 1)
('法定ビラ', 2)
('ビラ', 1)
('デマ', 4)
('?これ', 6)
('おつもり', 1)
('?#那覇市長選挙...', 1)
('mamakofans_kazu', 1)
('@0127soraru:', 1)
('yurikaero1', 1)
('#140秒動画#咲野', 1)
('花#さき', 1)
('#nonokasaki#お気に入り#エロ動画', 1)
('enutaak', 1)
('ロビン♪】ラジオ日本', 1)
('60try部', 1)
('10/18(木)17:55~21:00dj:土谷隼人さん', 1)
('岡田ロビン翔子さんゲスト:18時台', 1)
('吉川友さん19時台', 1)
('ザ・', 1)
('ちさ', 2)
('try@jorf.co.jp...', 1)
('unagiinu212', 1)
('@dreamidol_t:', 1)
('スリジエ候補生', 1)
('秋葉原プラム', 1)
('!出番前', 1)
('オフショット', 1)
('こちら!今日', 1)
('ユニットアー写風', 1)
('オーシャン', 2)
('漢字', 6)
('海', 5)
('山', 7)
('paty3150', 1)
('island5821', 1)
('@simatta_:', 1)
('mocchi_000', 1)
('@ryuryu006:', 1)
('#水着', 1)
('goodsnow01', 4)
('@suzudada_akita:', 1)
('~ef64-37', 1)
('arashidaniel', 1)
('@cchannel_tv:', 1)
('❗】', 1)
('ローラー', 1

('2倍', 1)
('民主党野田政権', 1)
('3党合意', 1)
('最高責任者', 1)
('野田首相', 1)
('民主党議員', 1)
('はえ', 1)
('民主党政権時代', 1)
('誤り', 7)
('明言', 4)
('風...', 1)
('daidaimyou', 1)
('天心十五さん(@arupaka9)', 1)
('タク君', 1)
('躍動感', 2)
('!顔', 1)
('#よそ', 2)
('#pixelart', 2)
('maru_cat2003', 2)
('@kaoru_akasaka:', 2)
('#シンクリ', 2)
('izm__________kb', 1)
('@kissbee_ticket:', 1)
('イベント情報解禁', 1)
('kissbee', 1)
('imaginism', 1)
('発売記念インストアイベント', 1)
('ミニライブ&特典会', 1)
('11月10日(土)15:30-/17:30-イオンレイクタウンkaze', 1)
('1階', 1)
('広場(埼玉)無料ミニライブ&特典会...', 1)
('matuno_123456_', 1)
('@73_73_73_73:', 2)
('ナメ', 1)
('しょー', 1)
('arm81007', 1)
('whaugusta', 2)
('@ono800:', 2)
('&gt;', 8)
('プサぐだ♀', 1)
('#odaibako', 2)
('リプライ', 15)
('マーリン', 2)
('くだり', 2)
('矛盾', 1)
('プサぐだにそこはかとないパパ', 1)
('み', 1)
('感知しま...', 1)
('dosei_dy', 1)
('@__oo_yun:', 1)
('急', 4)
('グラコロ期間', 1)
('ギルド様', 1)
('!職', 1)
('☞', 3)
('ミンス時間帯', 1)
('22時希望外部ツール', 1)
('discord', 2)
('専)', 1)
('#シノアリスギルド募集', 2)
('geruc3', 1)
('@rua_1105_zp:', 1)
('10月23日', 1)
('コラソンウェイvol.55場所', 1)
('渋谷ミルキーウェイ料

...

('ぷぁぃ', 1)
('ポぁぃ(bái)', 1)
('"没有"', 1)
('://t.co/dpopdvm6uj', 1)
('tego_kamikota', 1)
('@nozomu_9011:', 1)
('ジャニーズwest', 1)
('spot', 1)
('cm#ジャニーズwest', 1)
('#westival', 1)
('oyomesanchan', 1)
('ぉ!!#マシュマロ', 1)
('aiterasaki', 1)
('グロム', 2)
('試行錯誤', 1)
('д⊂)ハンドル', 1)
('ハンドル', 2)
('転倒', 1)
('jellyfishmaru', 2)
('@rina04060701:', 1)
('一日経過', 1)
('音沙汰一切無し', 1)
('...。音沙汰', 1)
('飼い主様', 1)
('@cocooperd', 1)
('kumo336', 1)
('__ukauta__', 1)
('harimaoanan', 1)
('卒業式', 1)
('white_choco_301', 1)
('ピューロ', 1)
('yume_yupoppo', 1)
('運勢www', 1)
('minziyong', 1)
('@mtoriofficial:', 1)
('スタッフチーム', 1)
('召喚条件', 1)
('発動条件', 1)
('オシリス', 1)
('ラー', 1)
('運営様', 1)
('オベリスク実装お願い', 1)
('@tajiri110', 2)
('yxoxko', 1)
('chinyadono', 1)
('snow_gbf_', 1)
('@htk390:', 1)
('光属性', 1)
('ゼウス', 1)
('リソース', 1)
('最近モチベ', 1)
('マグナ2', 1)
('最終', 1)
('あと雑食', 1)
('絶対大丈夫', 1)
('kounorey', 1)
('mini!', 1)
('#so34022632', 1)
('ぁぁん...みんな', 1)
('...3分アニメ', 1)
('matsuri34ori', 1)
('@hosomimuseum:', 1)
('次回展予告】\\', 1)
('前売チケット', 1)
('10/1

('声優men', 1)
('vol.12', 1)
('表紙&amp;巻頭', 1)
('柿原徹也さん', 1)
('独占グラビア&amp;インタビュー14p', 1)
('tail', 1)
('総力特集', 1)
('#フェアリーテ...', 1)
('bo9jk55dpspfh9h', 1)
('s_sunagawa', 1)
('ゾイfor画面', 1)
('ワイルドライガー', 1)
('zaod', 1)
('dekosan9', 1)
('@maryannemargot:', 1)
('嘘つき安倍晋三', 1)
('isamu_shimizu', 1)
('hellopro0001', 1)
('yu_ta_ro_0402', 1)
('@proud_roar:', 1)
('男酒場', 1)
('あかねちゃん', 1)
('cfzehx', 1)
('ツマガリクッキー', 1)
('(ケーキハウス', 1)
('ツマガリ)関西', 1)
('洋菓子店(兵庫県西宮市甲陽園', 1)
('本店)', 1)
('関東', 1)
('抜き持ち味', 1)
('自家製', 1)
('旨み', 1)
('安全性', 1)
('mayu_torihiki23', 1)
('@oha_asa_no1:', 1)
('リングライト', 1)
('ヨコハマ', 1)
('理鶯譲', 1)
('使用1点求', 1)
('もちころ', 1)
('独歩1点異種間', 1)
('差額(定価)', 1)
('精算', 1)
('もちころりん', 1)
('開封済み', 1)
('...)検索', 1)
('savumacchan', 1)
('@identityvtamama:', 1)
('ouixyafps2uvyl1', 1)
('前川喜平', 1)
('~】東京新聞', 1)
('望月衣塑子', 1)
('文科事務次官', 1)
('人事', 1)
('次官', 1)
('前川喜平氏', 1)
('加計学園獣医学部創設', 1)
('総理', 3)
('意向文書', 1)
('(当時)官房長', 1)
('藤原氏', 1)
('官邸', 1)
('問題視', 1)
('?」菅義', 1)
('官房...', 1)
('mikaguramomo', 1)
('@sc_hu

('#宙ガール', 1)
('#久万高原', 1)
('aisu_1234', 1)
('kiduki_i', 1)
('あさり', 1)
('鶏天(もも', 1)
(')☆', 1)
('びんちょう鮪', 1)
('煮付けハンバーグ', 1)
('ピリ辛ゴマ白菜(漬物)☆', 1)
('じみ', 1)
('s95ihdvughfxhoq', 1)
('@nuremoh:', 1)
('クライマックスシリーズ', 1)
('1号', 1)
('広島vs巨人', 1)
('ryuto08251111', 1)
('7hiburi', 1)
('(^ー^)', 1)
('seikemw5k0on1iy', 1)
('@basilico30541:', 1)
('ネトゲ', 1)
('(^ー^)#ガルパ', 1)
('#白金燐子', 1)
('#白金燐子生誕祭', 1)
('#バンドリーマー', 2)
('#バンドリーマー女子部...', 1)
('sg79l', 1)
('テイルズ好き', 1)
('ぁぼお', 1)
('#テイルズ', 1)
('tokyu9000series', 1)
('@hachimukoshin:', 1)
('八トタ201系', 1)
('8年', 1)
('豊田', 1)
('神体ことクハ201-1', 1)
('201系', 1)
('@akibasofmap_evt:', 1)
('放課後プリンセス', 1)
('プレゼント!店頭受け取り', 1)
('10/20(土)...', 1)
('amatake', 1)
('@irenehanabi:', 1)
('30度', 1)
('二度', 1)
('犬様方', 1)
('s_whiterook', 1)
('ブラックホーク社製', 1)
('v1ベスト', 1)
('1着', 1)
('¥19,800-マガジンフラップ', 1)
('全てウッドランド', 1)
('一見', 1)
('eagle', 1)
('nomorevery', 1)
('breezeasian', 1)
('@netsensor1:', 1)
('大谷昭宏', 1)
('(新聞', 1)
('軽減税率対象', 1)
(')新聞', 1)
('ここ十年', 1)
('何百万', 1)
('2%', 1)
('宅

('://t.co/podsfcvdwu', 1)
('pppopx', 1)
('@kitaco127:', 1)
('魔神', 1)
('神映画', 1)
('内紛', 1)
('城下', 1)
('救い', 1)
('勧善懲悪', 1)
('大映', 1)
('cg', 1)
('特撮時代劇', 1)
('高山良策', 1)
('魔人', 1)
('田中貞造', 1)
('特撮合成', 1)
('現出', 1)
('映像力', 1)
('saniwa_1356', 1)
('mochi_taro00', 1)
('収録後', 1)
('すもも予想', 1)
('funnygameante', 1)
('ミュウツー', 2)
('逆襲', 1)
('ミュウ', 1)
('ナチュラルクズ', 1)
('満場一致', 1)
('://t.co/is6y3u9z5c', 1)
('cynthia_114514', 1)
('@maitetsu_ps:', 2)
('lgnorea', 1)
('麺活', 1)
('宮城県仙台市荒町商店中華そば', 1)
('ふじ', 1)
('黒胡椒', 1)
('比内地鶏鶏油そば', 1)
('肉増しおしゃれ', 1)
('!白ふじそば', 1)
('油そば久々', 1)
('屋裏', 1)
('タンメン', 1)
('ameo_megane', 1)
('tomo_uq', 1)
('kwnnue', 1)
('@k_karasu:', 1)
('gekona0710', 1)
('mi_sa_ki_11', 1)
('osyarekawaiigaz', 1)
('@clubfashionable:', 1)
('sakaeru_16night', 1)
('@tsukako:', 1)
('キュアピース', 1)
('ジータちゃん', 1)
('aineryu', 1)
('@atelierhonoka:', 1)
('新着商品', 1)
('デザインホログラム', 1)
('トライアングル', 2)
('スターミックス', 1)
('1g', 1)
('クリスマスカラー', 1)
('レジン封入', 1)
('フィルム状', 1)
('♪#レジン', 1)
('#手芸', 1)
('#uvレジン...', 1)
('jumma

('#perfume_um', 1)
('#perfume#perfume好き', 1)
('#フォロバ100%', 1)
('papillon_danser', 1)
('@tilfinning:', 1)
('#blackclover', 1)
('#ブラッククローバ', 1)
('caprin', 1)
('@hanamomov3:', 1)
('3月31日', 1)
('ヒナさん(@s_weet_kitchen', 1)
('丹頂巫女ミク', 1)
('ちび雪ミク姉妹', 1)
('3女', 1)
('散々', 1)
('」#mdd...', 1)
('syun_10ry', 1)
('@jinnao107:', 1)
('配信者必見', 1)
('k09m03', 1)
('@eisya777:', 1)
('#余命2019年4月', 1)
('進撃好きさん', 1)
('山奥マーレ', 1)
('お迎え大変', 1)
('リツイートお迎え', 1)
('nonoka_1224', 1)
('前塾いってき', 1)
('チャック', 1)
('kiyoretousigatt', 1)
('yanamasaki', 1)
('!写真', 1)
('ピアニストみたい', 1)
('ザルコ', 1)
('そっ', 1)
('ヤマハ', 1)
('イベント今日?', 1)
('ayupon_pon_', 1)
('♡#18禁', 1)
('#エッチ', 1)
('tontonzettyou', 1)
('4dbbda4a', 1)
('s_takumi0924', 1)
('@nanoyet:', 1)
('手ブレ', 1)
('女神様方', 1)
('とも観', 1)
('!♡https://...', 1)
('arico201705', 1)
('ぉ!時差', 1)
('ai_syo3000', 1)
('@kushino_yui:', 1)
('コミコミスタジオさん', 2)
('特典付き', 1)
('rinrinpika2', 1)
('@86no_oogiri:', 1)
('14(ジューシー)', 1)
('mooooooo__45', 1)
('fuchswaldcrow', 1)
('raputann', 1)
('c2fojxac3otvcj

twitterユーザー名も除外する。
|(or)でもできる

In [15]:
char_filters=[UnicodeNormalizeCharFilter(),RegexReplaceCharFilter('http(s)?://([-\w]+\.)+[-\w]+(/[-\w ./?%&=]*)?',''),RegexReplaceCharFilter('@([\w]+)','')]
token_filters = [CompoundNounFilter(), LowerCaseFilter(), POSKeepFilter(['名詞']),TokenCountFilter(att='base_form')]
a = Analyzer(char_filters, tokenizer, token_filters)
with codecs.open('tweet.txt','r','utf8') as f:
    text=f.read()
    tokens = a.analyze(text)
    for token in tokens:
        print(token)

('futao02', 1)
('rt', 7386)
(':', 7125)
('女の子', 112)
('peg_pef_peg', 1)
('昨晩', 1)
('ウルグアイ戦直後', 1)
('無料配信', 5)
('スカサカ!ライブ.net', 1)
('レビュー動画', 1)
('youtube上', 1)
('視聴回数2万回', 1)
('岩政さん', 1)
('清水さん', 1)
('試合分析', 1)
('こと', 414)
('cs放送局', 1)
('予算', 1)
('無料配信番組', 1)
('製作', 3)
('...', 1063)
('darekasanno_', 1)
('次第', 3)
('たくさん', 34)
('反応お願い', 1)
('(', 222)
('..)"', 1)
('#フォロワーさん', 4)
('フォロワーさん', 23)
('私', 191)
('事気', 1)
('方', 345)
('繋', 5)
('たい', 2)
('#歌い手好き', 1)
('ox42477139', 1)
('(^o^)', 12)
('さ', 104)
('山本アットホーム', 12)
('はなし', 25)
('今回', 63)
('ばん', 12)
('slot_kantakun', 1)
('仕事', 50)
('ゲーム', 16)
('時間', 65)
('人', 342)
('中', 98)
('もの適当', 3)
('当選率2倍', 3)
('フォロー', 86)
('3倍', 4)
('抽選', 135)
('ff内優先', 3)
('誰', 57)
('参加', 154)
('期間', 6)
('10月31日', 9)
('当選者', 11)
('11月1日', 3)
('3日', 4)
('dm', 47)
('chigaya808', 1)
('目', 124)
('rippa_puritty', 1)
('gorituru_madygn', 1)
('来月', 8)
('美容雑誌', 1)
('ファッション誌', 1)
('付録', 10)
('既製品', 1)
('サンプル', 7)
('もの', 121)
('どれ', 14)
('得', 12)
('計算', 1)
('maquia', 1)
('美的

('!!→://t.co/7gwzc7t7ty', 1)
('____taketanuuuu', 1)
('9月15日', 2)
('クランクイン', 2)
('ドラマ&映画', 2)
('明治東亰恋伽', 2)
('先日15日(月)', 2)
('主演:伊原六花さん', 2)
('ラストカット', 2)
('クランクアップ!苦楽', 2)
('スタッフ', 21)
('別れ', 4)
('笑顔', 29)
('撮影終了', 2)
('#めいこい', 2)
('#めいどら', 2)
('#伊原六花', 2)
('#明...', 2)
('329_mo_imouto', 1)
('速報2019年1月1日', 2)
('劇場公演8周年', 2)
('劇場公演', 2)
('組閣実施決定nmb488thanniversarylive', 2)
('1999megucha', 1)
('祝コケ', 1)
('ラジオ出演】#アバウドゴケ', 1)
('放送内', 1)
('#みや', 3)
('へ', 1)
('思い', 6)
('吐露', 1)
('#トークアバウト', 1)
('352f0ab614f64c6', 1)
('才能', 15)
('人類', 10)
('yes!プリキュア5', 9)
('a0703t17', 1)
('100円均一', 1)
('バーベキュー用', 1)
('炭', 1)
('......。炭', 1)
('andgj086', 1)
('▶', 9)
('line', 25)
('id:krs040110年以上運営', 1)
('老舗人妻店', 1)
('出稼ぎ情報', 1)
('♪栃木県平均保証3万~6万バック5000円~10000円年齢20歳~55歳', 1)
('可能単価', 1)
('交渉可能', 1)
('採用率', 1)
('店舗', 4)
('mushroom_n', 1)
('7話', 2)
('at38kyo', 1)
('試合結果', 2)
('広島6-1巨人(17日', 1)
('マツダ)/csファイナル初戦', 1)
('アドバンテージ', 5)
('2勝目#carp', 1)
('moeluvxxx', 1)
('不思議', 11)
('世界絵図', 1)
('存在', 13)
('場所', 26)
('素朴',

('募集', 26)
('是非リプ', 1)
('声がけ', 6)
('参加者', 1)
('fxbit', 1)
('#暗号通貨', 1)
('詐欺コイン', 1)
('見分け方', 2)
('非常', 6)
('い動画', 1)
('⇒://t.co/4ctvts1wto', 1)
('mrmrmrmr4455', 1)
('都内', 3)
('ヘンタイ', 1)
('セフレ', 5)
('子宮', 2)
('勢い', 13)
('射精', 5)
('中出', 2)
('合格', 3)
('イキ', 1)
('#裏垢女子...', 1)
('z4o_x', 1)
('aoneko906', 1)
('anri_02402', 1)
('dokan_tm', 1)
('naruhiras', 1)
('クロッキー#クロッキー', 1)
('#sketch', 1)
('u24c', 1)
('awtjrb7pqpc7mh9', 1)
('filag2', 1)
('rena27_sy14_48g', 1)
('cakehouse77', 1)
('就職祝い', 1)
('hoshi_takaaya', 1)
('haru__rurur', 1)
('ヒッチコック', 1)
('music:ヨルシカ様', 1)
('歌:', 1)
('ニコカラ', 1)
('加工クオリティ', 1)
('!#ヨルシカ', 1)
('#拡散希望#歌い手さんmix師さん絵師さん動画師さん', 1)
('pさん', 3)
('rt#rt', 1)
('人全員フ...', 1)
('konoka48249937', 1)
('明後日', 2)
('19日', 5)
('10~15:00出勤', 1)
('!sweet', 1)
('xo', 1)
('grief', 1)
('koaku10', 1)
('アプリ出身', 1)
('akane199493', 1)
('飛び込み...画像⇒://t.co/hugx0zyzra', 1)
('4ssaultk', 1)
('ozora2kanon', 1)
('noboruhabatobi', 1)
('モバマス', 1)
('ブレスオブファイア5', 1)
('yokotomo0818', 1)
('昨日復活', 1)
('シナモンメルツ'

('/#天然魚', 5)
('赤シャリ祭!\\10/17(水)', 5)
('すし', 14)
('皿赤シャリ!ネタ本来', 5)
('味', 35)
('赤シャリ', 23)
('天然魚', 14)
('期間限定メニュー', 14)
('食事券', 6)
('!10/28', 5)
('mtmngetdz2m', 1)
('下書き', 2)
('#ラフ', 1)
('下書きペン入れ完成', 1)
('原稿過程', 1)
('monkey90051331', 2)
('おい', 2)
('ライダーイモダ君', 1)
('改造おい', 1)
('ロボ', 1)
('!特殊', 1)
('能力', 1)
('悪者', 1)
('iria_theoryyyyy', 1)
('捏造注意', 1)
('映像', 12)
('字幕', 3)
('山賊編', 1)
('1315_meganekko', 1)
('10/18発売gファンタジー11月号', 1)
('妖怪学校', 1)
('!」48話目掲載', 1)
('!酒呑童子', 1)
('安倍晴明編中編', 1)
('凜太郎', 1)
('過去回!今', 1)
('1番シリアス回', 1)
('!最新単行本7巻', 1)
('発売中!...', 1)
('spkazu2', 1)
('笑写真', 1)
('日々笑顔練習中', 1)
('下田', 1)
('お手数', 1)
('azu_butamen', 1)
('月影(', 1)
('ペン)', 1)
('samezakura', 1)
('シャム無常', 1)
('noro37500360', 1)
('ウチ', 9)
('愛犬', 4)
('10月15日朝方', 1)
('首', 6)
('琉球犬', 1)
('#琉球犬', 1)
('masutadojisan', 1)
('怪獣ラクガキ', 1)
('dai_ddd', 1)
('カレスコ凸3', 1)
('ss_m81', 1)
(';`)❤', 1)
('ayatakanisitey1', 1)
('封印', 4)
('カード', 8)
('時代', 7)
('_yumi1222_', 1)
('ハロウィンだらけ', 1)
('yuzukichococh', 1)
('youtube', 11)
('精神病棟',

('are?', 1)
('has', 2)
('answers', 1)
('#mikecheckmin...', 1)
('kochan5100', 1)
('vicstra62', 1)
('pon!', 1)
('おと', 1)
('jr.', 2)
('林翔太大野智', 1)
('完コピ披露', 1)
('usagi__ii', 1)
('ちょこちゃん', 1)
('ひさし', 1)
('sue_yellow_jump', 1)
('垢', 15)
('(27)', 1)
('関東//sjk//29日参戦5歳児アイドル', 1)
('ぇー', 4)
('っ子さん', 3)
('っ子さんrt', 1)
('人お迎え...', 1)
('may_twr', 1)
('ーー', 10)
('ーーー', 8)
('sayu_syumi_k', 1)
('kiitsu312', 1)
('デュラララ!!', 1)
('sa30094669', 1)
('民主党政権', 4)
('民進党', 1)
('野党', 3)
('bakhyun1029', 1)
('笑い声威勢', 1)
('jy67fzguh', 1)
('攻略', 3)
('物理', 1)
('?⇐', 1)
('凸', 2)
('ファイアーエムブレム', 1)
('://t.co/1yvedw3z4y', 1)
('eros_gf', 1)
('ゆ', 13)
('兄貴がち', 5)
('天才', 5)
('ドブ', 6)
('akix', 1)
('最新動画', 1)
('タンメン中本', 2)
('食い', 2)
('挑戦みなさん最後', 1)
('shungotorii', 1)
('ハスキー', 8)
('sgvitm3qnlr5kup', 1)
('長門...提督', 1)
('kurigohan80kg', 1)
('...ベリーソース好き', 1)
('チョコ', 3)
('ほんとオススメ', 1)
('wagamitinikibou', 1)
('秋田県', 2)
('北秋田市', 1)
('安', 1)
('滝#東北', 1)
('syuri_46', 1)
('帰り', 4)
('夜風', 1)
('黄昏', 2)
('気分', 8)
('こゆとき', 1)
('小雨', 1)
('

...

('nattan_ichigo', 1)
('piano_woodstock', 1)
('akipanmanyua090', 1)
('飛び込み...画像⇒://t.co/xzmi246aqo', 1)
('x1t84g4aly', 1)
('!みんなタニタ', 1)
('歩数計', 1)
('!!#中', 1)
('人一万歩', 1)
('競争', 1)
('pwhb2295', 1)
('キャンドルちゃん', 1)
('国内ps4版配信開始', 1)
('ロウソク', 1)
('10秒間', 1)
('アクション://t.co/1rypzh8tki', 1)
('scottie_fan', 1)
('makoto_igari', 1)
('紅葉早期相(10月中旬', 1)
('下旬)', 1)
('六十里峠', 1)
('変動', 1)
('位相', 1)
('樹種', 1)
('#只見線', 1)
('urumaniax', 1)
('3000人キャンペーン✨', 1)
('応募完了!!', 1)
('(匿名配送', 1)
('連絡)', 1)
('rt数30名毎', 1)
('1名抽選(例98rt', 1)
('場合3名抽選)', 1)
('zumu_1904', 1)
('渋谷wwwx', 1)
('ワンマンリハ', 1)
('見所', 1)
('...大人脇', 1)
('koma_aki_83', 1)
('本日発売!】', 1)
('1巻発売', 1)
('満載!▽...', 1)
('skybluemuku', 1)
('yama_noriakin', 1)
('hoshimiyasakura', 1)
('ati17mezo186m', 1)
('新刊サンプル', 1)
('2!!', 1)
('夜抄前', 1)
('スレ', 1)
('しょんぼり', 1)
('!#博麗神社秋季例大祭', 1)
('cyacoco1', 1)
('zunsu1130', 1)
('完', 1)
('致', 1)
('谷', 2)
('隼', 1)
('美', 1)
('説そ', 1)
('手勝', 1)
('利', 1)
('法', 1)
('則卓', 1)
('界', 1)
('救', 1)
('ryotaro3301', 1)
('69', 1)
('島本

('sunuko0922', 1)
('!#中野ジェームズ修一', 1)
('#徳間書店', 1)
('twice______1229', 1)
('ソンムル企画》☺', 1)
('rt+フォロー', 1)
('タワレコ', 1)
('3種類1', 1)
('合計3名様', 1)
('ソンムル', 1)
('!!!⚠', 1)
('全て公式', 1)
('summer...', 1)
('69de74__', 1)
('リリスク', 1)
('ニューツアーt', 1)
('5色!是非ゲト', 1)
('final仕様', 1)
('snow_vantis', 1)
('70', 1)
('!セブンシリーズ', 1)
('インゲン栽培', 1)
('usanezumi_2003', 1)
('親友', 1)
('airpods君', 1)
('......ケースどこぉぉぉおぉぉお', 1)
('〜!?', 1)
('seririnn77', 1)
('吉木りさタイプ', 1)
('key_talk_1005', 1)
('新作ポテンヒット', 1)
('きん', 1)
('#ゆず立ち://t.co/bpxp5xzmro', 1)
('pas_st_my', 1)
('キル(^o^)', 1)
('uzu_sabage', 1)
('問答無用', 1)
('ww(キョンシー', 1)
('0203actorlove', 1)
('yosinotaiyou', 1)
('コルチカム', 1)
('no_doubtfamily', 1)
('ぎゃん', 1)
('?長野さん', 1)
('!!#ジャー坊', 1)
('#大牟田', 1)
('#jabow', 1)
('#omuta', 1)
('#レベルファイブ', 1)
('hayatoootsuka', 1)
('場内騒然!', 2)
('オカダ', 2)
('棚橋', 2)
('yoh&sho', 2)
('タッグ王者', 2)
('金丸&デスペラード', 2)
('撃破!【10.17後楽園結果', 2)
('ocb0702', 1)
('♪.正解発表', 1)
('金澤朋子:...', 1)
('rumia334', 1)
('yukigonnnn_1127', 1)
('yudeebi001', 1)
('ラブリ

('フリーきっぷ', 1)
('運賃', 1)
('金額', 1)
('乗り放題', 1)
('#東方神起_livetour_2018_tomorro...', 1)
('nepu_kyo', 2)
('⛩', 1)
('#いろは絵馬', 1)
('vil_lie', 1)
('92d4b31e', 1)
('mky18mky', 1)
('凛太朗&由仁', 1)
('zcnx8s4lhxydzt1', 1)
('装備紹介!】大型製造解放', 1)
('防弾ベスト', 1)
('バックショット', 1)
('スラッグ弾', 1)
('!これら', 1)
('基本ショットガンタイプ', 1)
('人形', 1)
('限り装備', 1)
('tirotirokun9', 1)
('フォロワー様', 1)
('印', 1)
('marinelive_ft', 1)
('8回裏立正大', 1)
('キャプテン伊藤裕季也(4日大三)', 1)
('2ラン', 2)
('レフト', 1)
('特大', 1)
('大学最後', 1)
('打席', 1)
('豪快', 1)
('sunsakiii', 1)
('13背景', 1)
('ファッション雑誌', 1)
('絵師様', 1)
('uranogift', 1)
('junsei_rugby16', 1)
('merch#oneokrock', 1)
('gtspiatc320', 1)
('2018年7月17日配信分', 1)
('#川越紗彩', 1)
('aaaaatyi', 1)
('miyatya01', 1)
('kq2133kaitoku', 1)
('07t', 1)
('sui25', 1)
('_waaaaaaaasan', 1)
('前衛後衛特化ガチャ開催!】明日10/18', 1)
('前衛特化', 1)
('後衛特化', 1)
('開催!前衛', 1)
('後衛武器', 1)
('排出', 1)
('前衛後衛ガチャ限定', 1)
('追加!', 1)
('miniminimidorig', 1)
('48kuro', 1)
('piko_sansita', 1)
('武器つよ回', 1)
('日本有線大賞', 1)
('インフルエンサー', 1)
('嗅覚', 1)
('ブレイク', 1)
('予定外'

('siru2017', 1)
('akiくん', 1)
('あちら側みたい', 1)
('gyr121762659', 1)
('阿部顕嵐', 1)
('love-tune全員', 1)
('amanchuaqua', 1)
('肉棒', 1)
('豊か', 1)
('蜜壷', 1)
('至福', 1)
('ひと時', 1)
('庭園', 1)
('びふたりきりの空間', 1)
('愛人', 1)
('背徳的', 1)
('快楽', 1)
('#愛人', 1)
('#快楽', 1)
('km6oe6ug6hu5emf', 1)
('711worker', 1)
('colus06', 1)
('初日終了', 1)
('あと4日!】平日', 1)
('物販購入', 1)
('\\お待ち', 1)
('✨✨/#めめ猫展', 1)
('meteor841', 1)
('woozi_1122_kuro', 1)
("d('∀'*)idealcut日本韓国", 1)
('sc', 1)
('これプラス1枚別', 1)
('ライブトレカ', 1)
('yusa_yusa1488', 1)
('堅実', 1)
('立ち回り', 1)
('ゴミキルレ', 1)
('crowriusrealice', 1)
('学者コス', 1)
('あと箒', 1)
('エマさん無気力', 1)
("(●'▿'●)", 1)
('skyomame', 1)
('余ホテル', 1)
('泊まり', 1)
('kyohei118', 1)
('在日米軍司令官ジェリー', 1)
('マルティネス中将', 1)
('今年6月11日', 1)
('嘉手納基地所属', 1)
('f15戦闘機墜落事故', 1)
('緊急脱出', 1)
('パイロット1人', 1)
('救助', 1)
('航空自衛隊那覇基地所属', 1)
('救難隊員ら9人', 1)
('勲章', 1)
('授与', 1)
('hana97449805', 1)
('hw8tzxmm6cxbksf', 1)
('捜索中!→#愛知県', 1)
('#三ノ輪町', 1)
('興寺2h28.4.5迷子3メス4#三毛猫', 1)
('スペード', 1)
('サクラ耳', 1)
('首輪/名札', 1)
('inui_ruka', 1)
('sana_

('ドデスカ!」コメント出演', 1)
('!是非ご覧', 1)
('hinayuki__ura', 1)
('!!⛔', 1)
('card', 1)
('30人', 1)
('!!(ググカ変更可)⛔', 1)
('リツイート!...', 1)
('gingerale0818', 1)
('♥✌', 1)
('#james_ppt', 1)
('#lovebychanceseries', 1)
('lei_arks', 1)
('yukilin718', 1)
('[preview]', 1)
('#sungjong', 1)
('heading', 1)
('malaysia', 1)
("'sales", 1)
("tv'©monodrama", 1)
('kyo_chi_n', 1)
('hato0426', 1)
('makoto__1978', 1)
('www#', 1)
('#毎日投稿', 1)
('#読者募集中', 1)
('#イケメン風', 1)
('6__na__v', 1)
('!!参戦', 1)
('#東京ドーム', 1)
('#13日', 1)
('#サプライズ企画', 1)
('#armyさんスルー禁止', 1)
('azukotori', 1)
('レンタカー', 1)
('タイム', 1)
('anneisyuka', 1)
('【#hilcrhyme', 1)
('hill', 1)
('sns2次先行受付中!】', 1)
('2年ぶり', 1)
('全国ツアー', 1)
('2019年2月2日', 1)
('全国20箇所', 1)
('開催!sns先行', 1)
('申込み', 1)
('yak_makr', 1)
('0sakihitosi', 1)
('ドリンクホルダー', 1)
('akira0628_', 1)
('assaultfox', 1)
('antenanasi', 1)
('いつか何', 1)
('vanichan_lock', 1)
('nyotti_r', 1)
('便乗みたい', 1)
('···!(自分', 1)
('イベント等', 1)
('仕様変更前', 1)
('ぱりさんとmaliceさん)写真', 1)
('shellblog', 1)
('atdtmudt', 1)
('yaco0729',

dictionaryにして並び替える


In [17]:
with codecs.open('tweet_top1000.txt','r','utf8') as f:
    text=f.read()
    tc = dict(a.analyze(text))
    print(sorted(tc.items(),key=lambda x: x[1], reverse= True))

[('rt', 732), (':', 709), ('...', 108), ('!', 81), ('#', 70), ('の', 67), ('こと', 50), ('ん', 44), ('人', 38), ('!!', 28), ('これ', 27), ('今', 27), ('今日', 26), ('方', 25), ('(', 23), (')', 21), ('~', 21), ('ツイート', 20), ('参加', 19), ('お願い', 19), ('私', 18), ('よう', 17), ('❤', 16), ('動画', 16), ('こちら', 16), ('それ', 15), ('?', 15), ('ー', 14), ('中', 13), ('目', 13), ('好き', 13), ('登場', 13), ('前', 13), ('事', 13), ('明日', 13), ('女の子', 12), ('さ', 12), ('今回', 12), ('✨', 12), ('一緒', 12), ('日', 11), ('気', 11), ('感じ', 11), ('くじ', 11), ('何', 11), ('僕', 11), ('☺', 11), ('イベント', 11), ('時間', 10), ('10/17', 10), ('#ローソン', 10), ('トラウマ', 10), ('女子中学生', 10), ('同級生', 10), ('電車', 10), ('みたい', 10), ('自分', 10), ('本日', 10), ('さん', 10), ('はなし', 9), ('フォロー', 9), ('カスタード', 9), ('#ウチカフェ', 9), ('画像', 9), ('あなた', 9), ('時', 9), (':参戦id参加者募集!lv100', 9), ('そう', 9), ('写真', 9), ('❗', 9), ('声', 9), ('日本', 9), ('誰', 8), ('dm', 8), ('もの', 8), ('歌', 8), ('紹介', 8), ('23:59', 8), ('プレゼント', 8), ('結果', 8), ('視聴中', 8), ('w', 8), ('最後', 8), ('フ